In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pycountry

pd.set_option('display.max_rows', None)   # Shows all rows in the DataFrame
pd.set_option('display.max_columns', None)  # Shows all columns in the DataFrame
pd.set_option('display.width', None)     # Ensures no line breaks for wide DataFrames
pd.set_option('display.max_colwidth', None)

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier  # Use RandomForestRegressor for regression tasks
from sklearn.metrics import accuracy_score  # Or appropriate metrics for your problem


# Import Data

In [4]:
df = pd.read_csv('data/SAP Datasets.csv')

# forward and backward filling
years_col = [str(i) for i in range(2023,2024)]
df[years_col] = df[years_col].apply(lambda row: row.ffill().bfill(), axis=1)

# drop unnecessary columns
df = df.drop(['Country Code', 'short description', 'long description', 'Indicator Code'], axis=1)

/var/folders/ds/b8dd7ztn06l6p5dfvy90q01c0000gn/T/ipykernel_26218/3573807460.py:1: DtypeWarning: Columns (7) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('data/SAP Datasets.csv')


# Ranking by Indicators

In [5]:
Indicators = pd.read_csv('data/Indicators_final.csv')

Indicators = Indicators[Indicators['DOES A HIGHER VALUE INCREASE POVERTY?'] != 'TBD']
Indicators

INDICATOR NAMES  \
0                                                                   Control of Corruption: Estimate   
1                      Multilateral debt service (% of public and publicly guaranteed debt service)   
2                 Access to clean fuels and technologies for cooking, rural (% of rural population)   
3                 Access to clean fuels and technologies for cooking, urban (% of urban population)   
4                              Access to clean fuels and technologies for cooking (% of population)   
5                                              Access to electricity, rural (% of rural population)   
6                                              Access to electricity, urban (% of urban population)   
7                                                           Access to electricity (% of population)   
8                                                           Compensation of employees (current LCU)   
9                                                          Compensation of employees (% of expense)   
10                                            Adjusted savings: education expenditure (current US$)   
11                                            Adjusted net national income per capita (current US$)   
12                                                         Terms of trade adjustment (constant LCU)   
13  Adequacy of social protection and labor programs (% of total welfare of beneficiary households)   
14        Adequacy of unemployment benefits and ALMP (% of total welfare of beneficiary households)   
15            Adequacy of social safety net programs (% of total welfare of beneficiary households)   
16             Adequacy of social insurance programs (% of total welfare of beneficiary households)   
17                                  Political Stability and Absence of Violence/Terrorism: Estimate   
18                                            Literacy rate, youth female (% of females ages 15-24)   
19                                     Literacy rate, youth (ages 15-24), gender parity index (GPI)   
20                                                Literacy rate, youth male (% of males ages 15-24)   
21                                              Literacy rate, youth total (% of people ages 15-24)   
22                                     Literacy rate, adult female (% of females ages 15 and above)   
23                                         Literacy rate, adult male (% of males ages 15 and above)   
24                                       Literacy rate, adult total (% of people ages 15 and above)   
25                                                           Compulsory education, duration (years)   
29                                                                  Children out of school, primary   
30                                                          Children out of school, primary, female   
31                                  Children out of school, female (% of female primary school age)   
32                                                            Children out of school, primary, male   
33                                      Children out of school, male (% of male primary school age)   
34                                                 Children out of school (% of primary school age)   
35                       Adolescents out of school, female (% of female lower secondary school age)   
36                           Adolescents out of school, male (% of male lower secondary school age)   
37                                      Adolescents out of school (% of lower secondary school age)   
38                      Expenditure on primary education (% of government expenditure on education)   
39                    Expenditure on secondary education (% of government expenditure on education)   
40                     Expenditure on tertiary education (% of government expenditure on education)   
45                            People using at least basic drinking 

## Indicator Dataframes

In [6]:
results = {}

for index, row in Indicators.iterrows():
    indicator_name = row['INDICATOR NAMES']
    increase_poverty = row['DOES A HIGHER VALUE INCREASE POVERTY?']
    
    if increase_poverty == 'TBD':
        continue

    indicator_df = df[df['Indicator Name'] == indicator_name]
    indicator_df.set_index('Country Name', inplace=True)
    
    years_columns = [str(year) for year in range(2000, 2024)]
    country_year_data = indicator_df[years_columns]
    
    if increase_poverty == 'TRUE':
        direction = True  # Lower values get better ranks
    elif increase_poverty == 'FALSE':
        direction = False  # Higher values get better ranks
    
    ranked_countries = country_year_data.rank(axis=0, method='min', ascending=direction, na_option='keep')
    
    column_name = f"{indicator_name}"
    ranked_countries[column_name] = ranked_countries.mean(axis=1, skipna=True)
    
    results[column_name] = ranked_countries[[column_name]].sort_values(by='Country Name').reset_index()

In [7]:
combined_df = pd.concat([df.drop('Country Name', axis=1) for _, df in results.items()], axis=1)
combined_df.insert(0,'Country Name', results['Control of Corruption: Estimate']['Country Name'])

In [8]:
combined_df.head()

Country Name  Control of Corruption: Estimate  \
0                  Afghanistan                       192.318182   
1  Africa Eastern and Southern                              NaN   
2   Africa Western and Central                              NaN   
3                      Albania                       137.818182   
4                      Algeria                       136.590909   

   Multilateral debt service (% of public and publicly guaranteed debt service)  \
0                                                                    130.705882   
1                                                                           NaN   
2                                                                           NaN   
3                                                                     72.652174   
4                                                                     23.478261   

   Access to clean fuels and technologies for cooking, rural (% of rural population)  \
0                                                                         181.304348   
1                                                                         181.347826   
2                                                                         202.217391   
3                                                                         127.565217   
4                                                                          71.565217   

   Access to clean fuels and technologies for cooking, urban (% of urban population)  \
0                                                                         163.130435   
1                                                                         185.739130   
2                                                                         203.086957   
3                                                                         132.652174   
4                                                                          51.956522   

   Access to clean fuels and technologies for cooking (% of population)  \
0                                                            182.347826   
1                                                            186.478261   
2                                                            201.043478   
3                                                            131.434783   
4                                                             70.565217   

   Access to electricity, rural (% of rural population)  \
0                                            184.950000   
1                                            222.714286   
2                                            216.173913   
3                                             22.217391   
4                                            116.000000   

   Access to electricity, urban (% of urban population)  \
0                                            188.130435   
1                                            236.217391   
2                                            215.652174   
3                                             84.304348   
4                                             99.173913   

   Access to electricity (% of population)  \
0                               201.434783   
1                               238.043478   
2                               217.782609   
3                                57.391304   
4                               109.130435   

   Compensation of employees (current LCU)  \
0                                46.166667   
1                                      NaN   
2                                      NaN   
3                                55.142857   
4                                      NaN   

   Compensation of employees (% of expense)  \
0                                 84.833333   
1                                 36.357143   
2                                 45.857143   
3                                 70.500000   
4                                       NaN   

   Adjusted savings: education expenditure (current US$)  \


In [9]:
combined_df['Average_Rank'] = combined_df.iloc[:, 1:].mean(axis=1) 

combined_df_sorted = combined_df.sort_values(by='Average_Rank', ascending=True)

In [10]:
combined_df_sorted[['Country Name', 'Average_Rank']].reset_index()

index                                          Country Name  Average_Rank
0      212                                             Singapore     30.481617
1      235                                           Switzerland     31.531689
2       40                                        Cayman Islands     32.030170
3      173                                           Netherlands     34.414164
4      126                                           Korea, Rep.     34.825930
5       13                                             Australia     34.983952
6      110                                               Iceland     35.749793
7      153                                                 Malta     36.227518
8       58                                               Denmark     36.591764
9      196                                              Portugal     36.749640
10     147                                      Macao SAR, China     36.875054
11      88                                               Germany     37.155077
12      14                                               Austria     37.969121
13     182                                                Norway     38.434422
14     103                                  Hong Kong SAR, China     39.480446
15     251                                  United Arab Emirates     39.588507
16     200                                                 Qatar     39.669822
17     205                                            San Marino     39.742694
18      21                                               Belgium     40.018351
19      56                                                Cyprus     40.544093
20      81                                               Finland     40.562293
21     234                                                Sweden     40.626689
22     118                                                 Italy     40.997146
23      83                                                France     41.201365
24     255                                               Uruguay     41.220027
25     104                                               Hungary     41.280571
26     146                                            Luxembourg     41.715424
27     115                                               Ireland     42.321446
28      17                                               Bahrain     42.459514
29      38                                                Canada     43.079195
30     175                                           New Zealand     43.110322
31     215                                              Slovenia     43.132681
32     141                                         Liechtenstein     43.197728
33     128                                                Kuwait     43.637843
34     213                             Sint Maarten (Dutch part)     43.662879
35     223                                                 Spain     43.672840
36      24                                               Bermuda     43.809888
37       6                                               Andorra     44.235706
38     179                                         North America     44.299955
39     243                                   Trinidad and Tobago     44.312854
40      45                                                 Chile     44.872642
41      91                                                Greece     45.823140
42     195                                                Poland     46.019644
43     142                                             Lithuania     46.167653
44      31                                     Brunei Darussalam     46.235747
45     252                                        United Kingdom     46.236620
46      57                                               Czechia     46.379606
47     120                                                 Japan     46.581539
48     135                                                Latvia     46.846198
49      71                                             

In [11]:
combined_df.to_csv('data/country_initial_rankings.csv')
pd.read_csv('')

FileNotFoundError: [Errno 2] No such file or directory: ''

In [ ]:
pd.read_csv('data/df_transformed.csv')

Country Name Country Code  \
0                                             Afghanistan          AFG   
1                             Africa Eastern and Southern          AFE   
2                              Africa Western and Central          AFW   
3                                                 Albania          ALB   
4                                                 Algeria          DZA   
5                                          American Samoa          ASM   
6                                                 Andorra          AND   
7                                                  Angola          AGO   
8                                     Antigua and Barbuda          ATG   
9                                              Arab World          ARB   
10                                              Argentina          ARG   
11                                                Armenia          ARM   
12                                                  Aruba          ABW   
13                                              Australia          AUS   
14                                                Austria          AUT   
15                                             Azerbaijan          AZE   
16                                           Bahamas, The          BHS   
17                                                Bahrain          BHR   
18                                             Bangladesh          BGD   
19                                               Barbados          BRB   
20                                                Belarus          BLR   
21                                                Belgium          BEL   
22                                                 Belize          BLZ   
23                                                  Benin          BEN   
24                                                Bermuda          BMU   
25                                                 Bhutan          BTN   
26                                                Bolivia          BOL   
27                                 Bosnia and Herzegovina          BIH   
28                                               Botswana          BWA   
29                                                 Brazil          BRA   
30                                 British Virgin Islands          VGB   
31                                      Brunei Darussalam          BRN   
32                                               Bulgaria          BGR   
33                                           Burkina Faso          BFA   
34                                                Burundi          BDI   
35                                             Cabo Verde          CPV   
36                                               Cambodia          KHM   
37                                               Cameroon          CMR   
38                                                 Canada          CAN   
39                                 Caribbean small states          CSS   
40                                         Cayman Islands          CYM   
41                               Central African Republic          CAF   
42                         Central Europe and the Baltics          CEB   
43                                                   Chad          TCD   
44                                        Channel Islands          CHI   
45                                                  Chile          CHL   
46                                                  China          CHN   
47                                               Colombia          COL   
48                                                Comoros          COM   
49                                       Congo, Dem. Rep.          COD   
50                                            Congo, Rep.          COG   
51                                             Costa Rica          CRI   
52                                          Cote d'Ivoire          CIV   
53                                               